In [1]:
!rm -rf /kaggle/working/adversarial-patch-transferability

In [2]:
!git clone -b noiseinit https://github.com/AGAMPANDEYY/adversarial-patch-transferability.git

Cloning into 'adversarial-patch-transferability'...
remote: Enumerating objects: 681, done.
remote: Counting objects: 100% (196/196), done.
remote: Compressing objects: 100% (143/143), done.
remote: Total 681 (delta 134), reused 49 (delta 49), pack-reused 485 (from 2)
Receiving objects: 100% (681/681), 7.36 MiB | 33.81 MiB/s, done.
Resolving deltas: 100% (375/375), done.


In [3]:
!git fetch origin noiseinit
!git pull origin noiseinit

fatal: not a git repository (or any parent up to mount point /kaggle)
Stopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).
fatal: not a git repository (or any parent up to mount point /kaggle)
Stopping at filesystem boundary (GIT_DISCOVERY_ACROSS_FILESYSTEM not set).


In [4]:
!rm -rf /kaggle/working/logs
!rm -rf /kaggle/working/patch

In [5]:
%cd /kaggle/working

/kaggle/working


In [6]:
!cp -r /kaggle/input/original-repo/adversarial-patch-transferability /kaggle/working/

cp: cannot stat '/kaggle/input/original-repo/adversarial-patch-transferability': No such file or directory


In [7]:
%cd /kaggle/working/adversarial-patch-transferability

/kaggle/working/adversarial-patch-transferability


In [8]:
with open('dataset/cityscapes.py', 'w') as f:
    f.write("""
import os

import cv2
import numpy as np
from PIL import Image
import sys
sys.path.append('/kaggle/working/adversarial-patch-transferability')

import torch
from dataset.base_dataset import BaseDataset

class Cityscapes(BaseDataset):
    def __init__(self, 
                 root, 
                 list_path,
                 num_classes=19,
                 multi_scale=True, 
                 flip=True, 
                 ignore_label=255, 
                 base_size=2048, 
                 crop_size=(512, 1024),
                 scale_factor=16,
                 mean=[0.485, 0.456, 0.406], 
                 std=[0.229, 0.224, 0.225],
                 bd_dilate_size=4):

        super(Cityscapes, self).__init__(ignore_label, base_size,
                crop_size, scale_factor, mean, std,)

        self.root = root
        self.list_path = list_path
        self.num_classes = num_classes

        self.multi_scale = multi_scale
        self.flip = flip
        
        self.img_list = [line.strip().split() for line in open(root+list_path)]

        self.files = self.read_files()

        self.label_mapping = {-1: ignore_label, 0: ignore_label, 
                              1: ignore_label, 2: ignore_label, 
                              3: ignore_label, 4: ignore_label, 
                              5: ignore_label, 6: ignore_label, 
                              7: 0, 8: 1, 9: ignore_label, 
                              10: ignore_label, 11: 2, 12: 3, 
                              13: 4, 14: ignore_label, 15: ignore_label, 
                              16: ignore_label, 17: 5, 18: ignore_label, 
                              19: 6, 20: 7, 21: 8, 22: 9, 23: 10, 24: 11,
                              25: 12, 26: 13, 27: 14, 28: 15, 
                              29: ignore_label, 30: ignore_label, 
                              31: 16, 32: 17, 33: 18}
        self.class_weights = torch.FloatTensor([0.8373, 0.918, 0.866, 1.0345, 
                                        1.0166, 0.9969, 0.9754, 1.0489,
                                        0.8786, 1.0023, 0.9539, 0.9843, 
                                        1.1116, 0.9037, 1.0865, 1.0955, 
                                        1.0865, 1.1529, 1.0507])
        
        self.bd_dilate_size = bd_dilate_size
    
    def read_files(self):
        files = []
        if 'test' in self.list_path:
            for item in self.img_list:
                image_path = item
                name = os.path.splitext(os.path.basename(image_path[0]))[0]
                files.append({
                    "img": image_path[0],
                    "name": name,
                })
        else:
            for item in self.img_list:
                image_path, label_path = item
                name = os.path.splitext(os.path.basename(label_path))[0]
                files.append({
                    "img": image_path,
                    "label": label_path,
                    "name": name
                })
        return files
        
    def convert_label(self, label, inverse=False):
        temp = label.copy()
        if inverse:
            for v, k in self.label_mapping.items():
                label[temp == k] = v
        else:
            for k, v in self.label_mapping.items():
                label[temp == k] = v
        return label

    def __getitem__(self, index):
        item = self.files[index]
        name = item["name"]
        image = cv2.imread(os.path.join(self.root,item["img"]),
                           cv2.IMREAD_COLOR)
        size = image.shape

        if 'test' in self.list_path:
            image = self.input_transform(image)
            image = image.transpose((2, 0, 1))

            return image.copy(), np.array(size), name

        label = cv2.imread(os.path.join(self.root,item["label"]),
                           cv2.IMREAD_GRAYSCALE)
        label = self.convert_label(label)

        image, label, edge = self.gen_sample(image, label, 
                                self.multi_scale, self.flip, edge_size=self.bd_dilate_size)

        return image.copy(), label.copy(), edge.copy(), np.array(size), name

    
    def single_scale_inference(self, config, model, image):
        pred = self.inference(config, model, image)
        return pred


    def save_pred(self, preds, sv_path, name):
        preds = np.asarray(np.argmax(preds.cpu(), axis=1), dtype=np.uint8)
        for i in range(preds.shape[0]):
            pred = self.convert_label(preds[i], inverse=True)
            save_img = Image.fromarray(pred)
            save_img.save(os.path.join(sv_path, name[i]+'.png'))
    """)

In [9]:
with open('dataset/cityscapes.py', 'r') as f:
    data =f.readlines()

In [10]:
import torch
import torch.nn as nn
import torch.nn.functional as F
import sys
sys.path.append('/kaggle/working/adversarial-patch-transferability')
from utils.utils import setup_logging, get_config_from_yaml, process_config, print_config
#from trainer.trainer_sidewalk import PatchTrainer
from trainer.trainer_vit2cnn import PatchTrainer
import torch
import pickle

2025-09-09 05:58:55.648052: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:477] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
E0000 00:00:1757397535.869141      19 cuda_dnn.cc:8310] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
E0000 00:00:1757397535.936563      19 cuda_blas.cc:1418] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


>  Segformer Train 

In [11]:
model_names = ['segformer']  # <— train the ViT (SegFormer) target

for model in model_names:
    config = get_config_from_yaml('configs/config.yaml', model=model)
    main_logger = process_config(config)

    trainer = PatchTrainer(config, main_logger)  # <—
    adv_patch, iou_log = trainer.train()                       # returns (tensor, np.array)

    out_path = config.experiment.log_patch_address + config.model.name + ".p"
    pickle.dump((adv_patch.cpu(), iou_log), open(out_path, "wb"))

 ****************************************************************************** 
                  Experiments at 2025-09-09 05:59:08.952480
 ****************************************************************************** 
Hi, This is root.
After the configurations are successfully processed and dirs are created.
The pipeline of the project will begin now.
------------- :: Config for this run :: -----------------
----------------- experiment--------------------
name:Experiments
log_patch_address:/kaggle/working/adversarial-patch-transferability/Experiments/
device:cuda
----------------- model--------------------
name:segformer
hf_name:nvidia/segformer-b0-finetuned-cityscapes-1024-1024
segformer_name:segformer_b0
segformer_ckpt_dir:/kaggle/input/my_local_hf_segformer_dir
segformer_ckpt:/kaggle/input/segformer_b0_hf_style/my_state_dict.pth
----------------- dataset--------------------
name:cityscapes
root:/kaggle/input/cityscapes-for-segmentation/Cityscapes/
train:train.txt
test:test.txt


config.json: 0.00B [00:00, ?B/s]

pytorch_model.bin:   0%|          | 0.00/15.0M [00:00<?, ?B/s]

[Surrogate] Loaded CNN: pidnet_s


model.safetensors:   0%|          | 0.00/14.9M [00:00<?, ?B/s]

Start training | Total Epochs: 20 (Stage-1: 0–9, Stage-2(JS): 10–19) | Iterations/epoch: 2975
[Limiter] max_batches_per_epoch=300, max_epochs=10
Epoch 0: using Stage-1
/kaggle/working/adversarial-patch-transferability/trainer/trainer_vit2cnn.py:520: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.no_grad(), autocast(dtype=torch.float16):
/kaggle/working/adversarial-patch-transferability/trainer/trainer_vit2cnn.py:571: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with autocast(dtype=torch.float16):
/kaggle/working/adversarial-patch-transferability/trainer/trainer_vit2cnn.py:573: FutureWarning: `torch.cuda.amp.autocast(args...)` is deprecated. Please use `torch.amp.autocast('cuda', args...)` instead.
  with torch.no_grad(), autocast(dtype=torch.float16):
Epoch 0/20 || Batch 1/2975 || LR: 0.000e+00 || Atk: 0.0554 || Attn:-0

In [12]:
model_names = ['pidnet_s']
#model_names = ['icnet','bisenet_v1','bisenet_v2','segformer']
#model_names = ['segformer']
for model in model_names:
  ## getting the config file
  config = get_config_from_yaml('configs/config.yaml',model = model)
  #print_config(config)

  ## processing config to initialize directories for logs etc
  main_logger = process_config(config)

  ## training
  train_obj = PatchTrainer(config,main_logger)
  save = train_obj.train()
  pickle.dump( save, open(config.experiment.log_patch_address+config.model.name+".p", "wb" ) )

 ****************************************************************************** 
                  Experiments at 2025-09-09 10:03:40.791669
 ****************************************************************************** 
Hi, This is root.
After the configurations are successfully processed and dirs are created.
The pipeline of the project will begin now.
------------- :: Config for this run :: -----------------
----------------- experiment--------------------
name:Experiments
log_patch_address:/kaggle/working/adversarial-patch-transferability/Experiments/
device:cuda
----------------- model--------------------
name:pidnet_s
hf_name:nvidia/segformer-b0-finetuned-cityscapes-1024-1024
segformer_name:segformer_b0
segformer_ckpt_dir:/kaggle/input/my_local_hf_segformer_dir
segformer_ckpt:/kaggle/input/segformer_b0_hf_style/my_state_dict.pth
----------------- dataset--------------------
name:cityscapes
root:/kaggle/input/cityscapes-for-segmentation/Cityscapes/
train:train.txt
test:test.txt
v